# Machine Learning on IBM i with Scikit Learn and DB1

Original notebook: https://github.com/IBM/customer-churn-prediction/blob/master/notebooks/customer-churn-prediction.ipynb

In [21]:
%pwd

'/home/BENOIT/firstdemo-scikitlearn-ibmi'

In [23]:
# Dowload the original dataset if necessary
#!wget https://community.watsonanalytics.com/wp-content/uploads/2015/03/WA_Fn-UseC_-Telco-Customer-Churn.csv  --no-check-certificate

# Load Dataframe from Db2

In [13]:
import ibm_db_dbi as dbi
import pandas as pd

# Telco Churn dataset from a CRM datasource - here Db2 for i in CHURN/CUSTCHURN2 7044 records

sql="SELECT * from CHURN.CUSTCHURN3"
pd.set_option('display.max_columns', 30)
try:
    conn = dbi.connect()
    df_fromdb2 = pd.read_sql(sql, conn)
    #print(df_fromdb2)
    df_fromdb2.info()
    
except Exception as err:
    print('Error'+ str(err))

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7043 entries, 0 to 7042
Data columns (total 21 columns):
CUSTOMERID          7043 non-null object
GENDER              7043 non-null object
SENIORCITIZEN       7043 non-null float64
PARTNER             7043 non-null object
DEPENDENTS          7043 non-null object
TENURE              7043 non-null float64
PHONESERVICE        7043 non-null object
MULTIPLELINES       7043 non-null object
INTERNETSERVICE     7043 non-null object
ONLINESECURITY      7043 non-null object
ONLINEBACKUP        7043 non-null object
DEVICEPROTECTION    7043 non-null object
TECHSUPPORT         7043 non-null object
STREAMINGTV         7043 non-null object
STREAMINGMOVIES     7043 non-null object
CONTRACT            7043 non-null object
PAPERLESSBILLING    7043 non-null object
PAYMENTMETHOD       7043 non-null object
MONTHLYCHARGES      7043 non-null float64
TOTALCHARGES        7043 non-null float64
CHURN               7043 non-null object
dtypes: float64(4), object(1

# 1-7_prepare_data_create_train_set.py

In [24]:
# Import packages & libraries 
import os
import pandas as pd
from pandas import Series, DataFrame
#import pandas_profiling

pd.set_option('display.max_rows', None,'display.max_columns', None)

import numpy as np

from collections import Counter

from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC, LinearSVC
from sklearn.ensemble import RandomForestClassifier, AdaBoostClassifier, GradientBoostingClassifier, ExtraTreesClassifier, VotingClassifier
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.tree import DecisionTreeClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import GridSearchCV, cross_val_score, StratifiedKFold, learning_curve, cross_validate
from sklearn.metrics import confusion_matrix, precision_score, recall_score, f1_score, make_scorer, roc_auc_score,accuracy_score, roc_curve
from scipy.stats import ks_2samp

from sklearn.preprocessing import Imputer, StandardScaler
#from sklearn import cross_validation
from sklearn import metrics

import os
import pandas as pd
import numpy as np
from sklearn import preprocessing, svm
from itertools import combinations
from sklearn.preprocessing import PolynomialFeatures, LabelEncoder, StandardScaler
import sklearn.feature_selection
from sklearn.model_selection import train_test_split
from collections import defaultdict
from sklearn import metrics
customer_data= pd.read_csv('WA_Fn-UseC_-Telco-Customer-Churn.csv')
pd.set_option('display.max_columns', 30)
customer_data.head(10)
customer_data = customer_data.drop('customerID', axis=1)
customer_data.head(5)
new_col = pd.to_numeric(customer_data.iloc[:, 18], errors='coerce')
new_col
customer_data.iloc[:, 18] = pd.Series(new_col)
customer_data
customer_data.isnull().values.any()

from sklearn.preprocessing import Imputer

imp = Imputer(missing_values="NaN", strategy="mean")

customer_data.iloc[:, 18] = imp.fit_transform(customer_data.iloc[:, 18].values.reshape(-1, 1))
customer_data.iloc[:, 18] = pd.Series(customer_data.iloc[:, 18])
customer_data.isnull().values.any()
customer_data.info()
pd.set_option('precision', 3)
customer_data.describe()
customer_data.describe(exclude=np.number)
customer_data.corr(method='pearson')
display(customer_data)

customer_data_encoded = pd.get_dummies(customer_data)
customer_data_encoded.head(10)

# Create training data for non-preprocessed approach
X_npp = customer_data.iloc[:, :-1].apply(LabelEncoder().fit_transform)
pd.DataFrame(X_npp).head(5)

# Create training data for that will undergo preprocessing
X = customer_data_encoded.iloc[:, :-2]
X.head()

# Extract labels
y_unenc = customer_data['Churn']

# Convert strings of 'yes' and 'no' to binary values of 0 or 1
le = preprocessing.LabelEncoder()
le.fit(y_unenc)

y_le = le.transform(y_unenc)
pd.DataFrame(y_le)




/QOpenSys/pkgs/lib/python3.6/site-packages/sklearn/ensemble/weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7043 entries, 0 to 7042
Data columns (total 20 columns):
gender              7043 non-null object
SeniorCitizen       7043 non-null int64
Partner             7043 non-null object
Dependents          7043 non-null object
tenure              7043 non-null int64
PhoneService        7043 non-null object
MultipleLines       7043 non-null object
InternetService     7043 non-null object
OnlineSecurity      7043 non-null object
OnlineBackup        7043 non-null object
DeviceProtection    7043 non-null object
TechSupport         7043 non-null object
StreamingTV         7043 non-null object
StreamingMovies     7043 non-null object
Contract            7043 non-null object
PaperlessBilling    7043 non-null object
PaymentMethod       7043 non-null object
MonthlyCharges      7043 non-null float64
TotalCharges        7043 non-null float64
Churn               7043 non-null object
dtypes: float64(2), int64(2), object(16)
memory usage: 1.1+ MB


gender  SeniorCitizen Partner Dependents  tenure PhoneService  \
0     Female              0     Yes         No       1           No   
1       Male              0      No         No      34          Yes   
2       Male              0      No         No       2          Yes   
3       Male              0      No         No      45           No   
4     Female              0      No         No       2          Yes   
5     Female              0      No         No       8          Yes   
6       Male              0      No        Yes      22          Yes   
7     Female              0      No         No      10           No   
8     Female              0     Yes         No      28          Yes   
9       Male              0      No        Yes      62          Yes   
10      Male              0     Yes        Yes      13          Yes   
11      Male              0      No         No      16          Yes   
12      Male              0     Yes         No      58          Yes   
13      Male              0      No         No      49          Yes   
14      Male              0      No         No      25          Yes   
15    Female              0     Yes        Yes      69          Yes   
16    Female              0      No         No      52          Yes   
17      Male              0      No        Yes      71          Yes   
18    Female              0     Yes        Yes      10          Yes   
19    Female              0      No         No      21          Yes   
20      Male              1      No         No       1           No   
21      Male              0     Yes         No      12          Yes   
22      Male              0      No         No       1          Yes   
23    Female              0     Yes         No      58          Yes   
24      Male              0     Yes        Yes      49          Yes   
25    Female              0      No         No      30          Yes   
26      Male              0     Yes        Yes      47          Yes   
27      Male              0     Yes        Yes       1           No   
28      Male              0     Yes         No      72          Yes   
29    Female              0      No        Yes      17          Yes   
30    Female              1     Yes         No      71          Yes   
31      Male              1     Yes         No       2          Yes   
32    Female              0     Yes        Yes      27          Yes   
33      Male              0      No         No       1          Yes   
34      Male              1      No         No       1          Yes   
35    Female              0     Yes        Yes      72          Yes   
36      Male              0      No         No       5          Yes   
37    Female              0      No         No      46          Yes   
38      Male              0      No         No      34          Yes   
39    Female              0      No         No      11          Yes   
40      Male              0     Yes        Yes      10          Yes   
41    Female              0     Yes        Yes      70          Yes   
42    Female              0     Yes        Yes      17          Yes   
43    Female              0      No         No      63          Yes   
44    Female              0     Yes         No      13          Yes   
45    Female              0      No         No      49          Yes   
46      Male              0      No         No       2          Yes   
47    Female              0      No         No       2          Yes   
48      Male              0      No         No      52          Yes   
49    Female              0     Yes        Yes      69          Yes   
50    Female              1      No         No      43          Yes   
51    Female              0      No         No      15          Yes   
52    Female              1     Yes         No      25          Yes   
53    Female              1     Yes         No       8          Yes   
54    Female              1     Yes        Yes      60          Yes   
55      Male              1   

0
0     0
1     0
2     1
3     0
4     1
5     1
6     0
7     0
8     1
9     0
10    0
11    0
12    0
13    1
14    0
15    0
16    0
17    0
18    1
19    0
20    1
21    0
22    1
23    0
24    0
25    0
26    1
27    1
28    0
29    1
30    0
31    0
32    0
33    0
34    0
35    0
36    1
37    0
38    1
39    1
40    0
41    0
42    0
43    0
44    0
45    0
46    0
47    1
48    0
49    0
50    0
51    1
52    0
53    1
54    0
55    1
56    0
57    0
58    0
59    0
60    0
61    0
62    0
63    0
64    1
65    0
66    0
67    0
68    0
69    0
70    0
71    0
72    0
73    0
74    0
75    0
76    0
77    0
78    0
79    0
80    1
81    0
82    1
83    0
84    0
85    0
86    0
87    0
88    0
89    0
90    0
91    0
92    0
93    0
94    0
95    1
96    0
97    1
98    0
99    1
100   0
101   0
102   0
103   0
104   1
105   0
106   0
107   0
108   0
109   0
110   1
111   0
112   0
113   1
114   0
115   0
116   0
117   1
118   0
119   0
120   0
121   0
122   1
123   0
124   0
125   0
126   1
127   0
128   0
129   0
130   0
131   1
132   0
133   1
134   1
135   0
136   0
137   0
138   0
139   1
140   0
141   1
142   0
143   0
144   0
145   0
146   0
147   1
148   0
149   0
150   0
151   1
152   0
153   0
154   0
155   0
156   0
157   0
158   0
159   0
160   0
161   1
162   0
163   0
164   0
165   0
166   1
167   0
168   1
169   0
170   0
171   1
172   0
173   1
174   0
175   0
176   1
177   1
178   0
179   0
180   1
181   0
182   1
183   0
184   1
185   1
186   0
187   0
188   0
189   0
190   0
191   1
192   0
193   0
194   0
195   0
196   0
197   0
198   0
199   0
200   0
201   0
202   0
203   0
204   0
205   0
206   0
207   1
208   1
209   0
210   1
211   0
212   0
213   0
214   0
215   0
216   0
217   0
218   0
219   0
220   1
221   0
222   0
223   1
224   0
225   0
226   0
227   1
228   0
229   0
230   0
231   0
232   1
233   0
234   0
235   1
236   0
237   0
238   1
239   0
240   0
241   0
242   0
243   0
244   0
245   0
246   0
247   1
248   1
249   0
250   0
251   1
252   1
253   0
254   0
255   0
256   0
257   0
258   1
259   0
260   1
261   1
262   0
263   0
264   0
265   0
266   0
267   0
268   1
269   0
270   1
271   0
272   1
273   0
274   1
275   1
276   1
277   0
278   0
279   0
280   0
281   0
282   0
283   0
284   1
285   0
286   0
287   1
288   1
289   1
290   1
291   0
292   0
293   0
294   0
295   0
296   0
297   0
298   0
299   1
300   0
301   1
302   0
303   0
304   0
305   0
306   1
307   0
308   0
309   0
310   0
311   0
312   0
313   0
314   1
315   0
316   0
317   1
318   1
319   0
320   1
321   0
322   0
323   0
324   0
325   0
326   0
327   1
328   0
329   0
330   0
331   0
332   0
333   1
334   1
335   1
336   1
337   0
338   0
339   1
340   0
341   0
342   0
343   0
344   0
345   0
346   1
347   0
348   0
349   0
350   0
351   0
352   0
353   1
354   1
355   1
356   0
357   0
358   1
359   0
360   0
361   0
362   0
363   0
364   0
365   1
366   0
367   0
368   0
369   0
370   0
371   1
372   0
373   0
374   0
375   0
376   0
377   1
378   0
379   0
380   0
381   1
382   0
383   1
384   0
385   1
386   1
387   0
388   0
389   0
390   0
391   0
392   0
393   0
394   0
395   0
396   0
397   1
398   0
399   0
400   0
401   0
402   1
403   0
404   0
405   0
406   0
407   0
408   1
409   1
410   1
411   0
412   0
413   0
414   0
415   0
416   0
417   0
418   1
419   1
420   0
421   0
422   0
423   0
424   0
425   0
426   0
427   0
428   0
429   0
430   1
431   0
432   0
433   1
434   0
435   0
436   0
437   0
438   0
439   0
440   0
441   0
442   0
443   0
444   0
445   1
446   1
447   0
448   0
449   0
450   0
451   0
452   0
453   1
454   0
455   0
456   0
457   0
458   0
459   0
460   0
461   0
462   1
463   1
464   0
465   0
466   0
467   0
468   0
469   1
470   0
471   1
472   0
473   0
474   1
475   1
476   0
477   0
478   1
479   1
480   0
481   1
482   0
483   0
484   1
485   0
486   0
487   0
488   0
489   1
490   0
491   0
492   1
493   0
494   0
495   1
496   0
497   0
498   1
499   

# 8-9_feature_engineering.py

In [26]:

# Find interactions between current features and append them to the dataframe
def add_interactions(dataset):
    # Get feature names
    comb = list(combinations(list(dataset.columns), 2))
    col_names = list(dataset.columns) + ['_'.join(x) for x in comb]
    
    # Find interactions
    poly = PolynomialFeatures(interaction_only=True, include_bias=False)
    dataset = poly.fit_transform(dataset)
    dataset = pd.DataFrame(dataset)
    dataset.columns = col_names
    
    # Remove interactions with 0 values
    no_inter_indexes = [i for i, x in enumerate(list((dataset ==0).all())) if x]
    dataset = dataset.drop(dataset.columns[no_inter_indexes], axis=1)
    
    return dataset


X_inter = add_interactions(X)
X_inter.head(15)

# Select best features
select = sklearn.feature_selection.SelectKBest(k=25)
selected_features = select.fit(X_inter, y_le)
indexes = selected_features.get_support(indices=True)
col_names_selected = [X_inter.columns[i] for i in indexes]

X_selected = X_inter[col_names_selected]
X_selected.head(10)





tenure  OnlineSecurity_No  TechSupport_No  Contract_Month-to-month  \
0     1.0                1.0             1.0                      1.0   
1    34.0                0.0             1.0                      0.0   
2     2.0                0.0             1.0                      1.0   
3    45.0                0.0             0.0                      0.0   
4     2.0                1.0             1.0                      1.0   
5     8.0                1.0             1.0                      1.0   
6    22.0                1.0             1.0                      1.0   
7    10.0                0.0             1.0                      1.0   
8    28.0                1.0             0.0                      1.0   
9    62.0                0.0             1.0                      0.0   

   MonthlyCharges_OnlineSecurity_No  MonthlyCharges_TechSupport_No  \
0                             29.85                          29.85   
1                              0.00                          56.95   
2                              0.00                          53.85   
3                              0.00                           0.00   
4                             70.70                          70.70   
5                             99.65                          99.65   
6                             89.10                          89.10   
7                              0.00                          29.75   
8                            104.80                           0.00   
9                              0.00                          56.15   

   MonthlyCharges_Contract_Month-to-month  Dependents_No_OnlineSecurity_No  \
0                                   29.85                              1.0   
1                                    0.00                              0.0   
2                                   53.85                              0.0   
3                                    0.00                              0.0   
4                                   70.70                              1.0   
5                                   99.65                              1.0   
6                                   89.10                              0.0   
7                                   29.75                              0.0   
8                                  104.80                              1.0   
9                                    0.00                              0.0   

   Dependents_No_TechSupport_No  Dependents_No_Contract_Month-to-month  \
0                           1.0                                    1.0   
1                           1.0                                    0.0   
2                           1.0                                    1.0   
3                           0.0                                    0.0   
4                           1.0                                    1.0   
5                           1.0                                    1.0   
6                           0.0                                    0.0   
7                           1.0                                    1.0   
8                           0.0                                    1.0   
9                           0.0                                    0.0   

   PhoneService_Yes_Contract_Month-to-month  \
0                                       0.0   
1                                       0.0   
2                                       1.0   
3                                       0.0   
4                                       1.0   
5                                       1.0   
6                                       1.0   
7                                       0.0   
8                                       1.0   
9                                       0.0   

   InternetService_Fiber optic_OnlineSecurity_No  \
0                                            0.0   
1                                            0.0   
2                                            0.0   
3                           

# 8-9_feature_engineering.py

In [27]:

# Find interactions between current features and append them to the dataframe
def add_interactions(dataset):
    # Get feature names
    comb = list(combinations(list(dataset.columns), 2))
    col_names = list(dataset.columns) + ['_'.join(x) for x in comb]
    
    # Find interactions
    poly = PolynomialFeatures(interaction_only=True, include_bias=False)
    dataset = poly.fit_transform(dataset)
    dataset = pd.DataFrame(dataset)
    dataset.columns = col_names
    
    # Remove interactions with 0 values
    no_inter_indexes = [i for i, x in enumerate(list((dataset ==0).all())) if x]
    dataset = dataset.drop(dataset.columns[no_inter_indexes], axis=1)
    
    return dataset


X_inter = add_interactions(X)
X_inter.head(15)

# Select best features
select = sklearn.feature_selection.SelectKBest(k=25)
selected_features = select.fit(X_inter, y_le)
indexes = selected_features.get_support(indices=True)
col_names_selected = [X_inter.columns[i] for i in indexes]

X_selected = X_inter[col_names_selected]
X_selected.head(10)





tenure  OnlineSecurity_No  TechSupport_No  Contract_Month-to-month  \
0     1.0                1.0             1.0                      1.0   
1    34.0                0.0             1.0                      0.0   
2     2.0                0.0             1.0                      1.0   
3    45.0                0.0             0.0                      0.0   
4     2.0                1.0             1.0                      1.0   
5     8.0                1.0             1.0                      1.0   
6    22.0                1.0             1.0                      1.0   
7    10.0                0.0             1.0                      1.0   
8    28.0                1.0             0.0                      1.0   
9    62.0                0.0             1.0                      0.0   

   MonthlyCharges_OnlineSecurity_No  MonthlyCharges_TechSupport_No  \
0                             29.85                          29.85   
1                              0.00                          56.95   
2                              0.00                          53.85   
3                              0.00                           0.00   
4                             70.70                          70.70   
5                             99.65                          99.65   
6                             89.10                          89.10   
7                              0.00                          29.75   
8                            104.80                           0.00   
9                              0.00                          56.15   

   MonthlyCharges_Contract_Month-to-month  Dependents_No_OnlineSecurity_No  \
0                                   29.85                              1.0   
1                                    0.00                              0.0   
2                                   53.85                              0.0   
3                                    0.00                              0.0   
4                                   70.70                              1.0   
5                                   99.65                              1.0   
6                                   89.10                              0.0   
7                                   29.75                              0.0   
8                                  104.80                              1.0   
9                                    0.00                              0.0   

   Dependents_No_TechSupport_No  Dependents_No_Contract_Month-to-month  \
0                           1.0                                    1.0   
1                           1.0                                    0.0   
2                           1.0                                    1.0   
3                           0.0                                    0.0   
4                           1.0                                    1.0   
5                           1.0                                    1.0   
6                           0.0                                    0.0   
7                           1.0                                    1.0   
8                           0.0                                    1.0   
9                           0.0                                    0.0   

   PhoneService_Yes_Contract_Month-to-month  \
0                                       0.0   
1                                       0.0   
2                                       1.0   
3                                       0.0   
4                                       1.0   
5                                       1.0   
6                                       1.0   
7                                       0.0   
8                                       1.0   
9                                       0.0   

   InternetService_Fiber optic_OnlineSecurity_No  \
0                                            0.0   
1                                            0.0   
2                                            0.0   
3                           

# 10-11_split_scale.py

In [28]:
#Split Data
X_train, X_test, y_train, y_test = train_test_split(X_selected, y_le,\
                                                    test_size=0.33, random_state=42)
print(X_train.shape, y_train.shape)
print(X_test.shape, y_test.shape)

# Use StandardScaler
scaler = preprocessing.StandardScaler().fit(X_train, y_train)
X_train_scaled = scaler.transform(X_train)

pd.DataFrame(X_train_scaled, columns=X_train.columns).head()
pd.DataFrame(y_train).head()



(4718, 25) (4718,)
(2325, 25) (2325,)


0
0  0
1  1
2  0
3  1
4  0

# 12_build_SVC_ClassifierModel.py

In [29]:

#Support Vector Macines on preprocessed data
from sklearn.svm import SVC
# Run classifier
clf_svc = svm.SVC(random_state=42)
clf_svc.fit(X_train_scaled, y_train)


SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='rbf',
  max_iter=-1, probability=False, random_state=42, shrinking=True,
  tol=0.001, verbose=False)

# 13_evaluate_SVC_ClassifierModel.py

In [30]:


# Use the scaler fit on trained data to scale our test data
X_test_scaled = scaler.transform(X_test)
pd.DataFrame(X_test_scaled, columns=X_train.columns).head()

# Get accuracy score
from sklearn.metrics import accuracy_score
# Get model confidence of predictions
y_score_svc = clf_svc.decision_function(X_test_scaled)
y_score_svc

# Get Precision vs. Recall score
from sklearn.metrics import average_precision_score
# Get accuracy score
y_pred_svc = clf_svc.predict(X_test_scaled)
acc_svc = accuracy_score(y_test, y_pred_svc)
print(acc_svc)

# Get Precision vs. Recall score
average_precision_svc = average_precision_score(y_test, y_score_svc)

print('Average precision-recall score: {0:0.2f}'.format(
      average_precision_svc))



0.8008602150537635
Average precision-recall score: 0.65


# 14_inference_SVC_ClassifierModel.py

In [31]:
import numpy as np

XInfer= np.array([[20.0, 0.0, 1.0, 0.0, 60.55, 10.0, 15.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]])
print("Support Vector Machine (aka Scikit Learn SVC) Model Inference - Telco Churn on IBM i 7.3")
print("Input Data to classify:", end="")
print(XInfer)
print("Result (Class):", end="")
print(clf_svc.predict(XInfer))
	


Support Vector Machine (aka Scikit Learn SVC) Model Inference - Telco Churn on IBM i 7.3
Input Data to classify:[[20.    0.    1.    0.   60.55 10.   15.    0.    0.    0.    0.    0.
   1.    1.    1.    1.    0.    0.    0.    0.    0.    0.    0.    0.
   0.  ]]
Result (Class):[0]


# 15_persist_SVC_ClassifierModel.py

In [34]:

from joblib import dump, load
dump(clf_svc, './SVC_Model_CHURN_IBMi_V1.joblib') 


['./SVC_Model_CHURN_IBMi_V1.joblib']

# 16_load_SVC_ClassifierModel.py

In [35]:
from joblib import load
clf_svc = load('SVC_Model_CHURN_IBMi_V1.joblib') 

# Test the Model

In [36]:
#XInfer=pd.DataFrame(X_train_scaled, columns=X_train.columns).head(20).values                                                                                                              
#print(clf_svc.predict(XInfer))                                                                                                                                                            
#[0 0 0 1 0 1 0 0 0 0 0 1 0 1 0 1 0 0 0 0]

#X_train_scaled.shape                                                                                                                                                                      
#(4718, 25)

X_test_scaled.shape                                                                                                                                                                       
#(2325, 25)
print("Testing model on IBM i")
print("Test Dataset:")
print(X_test_scaled)

XInfer=pd.DataFrame(X_test_scaled, columns=X_train.columns).head(20).values                                                                                                               
print("Result on 20 examples")
print(clf_svc.predict(XInfer))                                                                                                                                                            
#[1 0 0 1 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 1]


Testing model on IBM i
Test Dataset:
[[-1.28371441  1.01408821  1.0205589  ...  1.75838963  1.32508155
   1.69234921]
 [ 0.34821095 -0.98610751 -0.97985526 ... -0.56870217  1.32508155
  -0.59089459]
 [ 0.79699042 -0.98610751 -0.97985526 ... -0.56870217 -0.75467053
  -0.59089459]
 ...
 [-1.0389256   1.01408821  1.0205589  ... -0.56870217  1.32508155
  -0.59089459]
 [-0.01897226  1.01408821  1.0205589  ... -0.56870217  1.32508155
  -0.59089459]
 [ 1.08257736 -0.98610751  1.0205589  ...  1.75838963  1.32508155
   1.69234921]]
Result on 20 examples
[1 0 0 1 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 1]
